In [1]:
import pickle
import urllib.parse
import urllib.request
import requests
import _pickle as cPickle
import numpy as np

In [2]:
v_enc_embedding = pickle.load(open(f'/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/data/science/paths.pkl', 'rb'), encoding='latin1')

In [3]:
keys = v_enc_embedding.keys()
key_list = list(keys)
key_list[0]

'35540'

In [4]:
embedding = v_enc_embedding['35540']
embedding

{'forward': {'text': 'State is a synonym of Country. Country is related to Field. Field is related to Soccer. ',
  'short': 'State <--Synonym--> Country <--RelatedTo--> Field <--RelatedTo--> Soccer '},
 'reverse': {'text': 'Soccer is related to Field. Field is related to Country. Country is a synonym of State. ',
  'short': 'Soccer <--RelatedTo--> Field <--RelatedTo--> Country <--Synonym--> State '}}

In [5]:
entity_qid_dict = dict()
def get_entity_qid(entity):
    if entity in entity_qid_dict:
        return entity_qid_dict[entity]
    params = dict (
            action='wbsearchentities',
            format='json',
            language='en',
            uselang='en',
            search= entity
            )

    response = requests.get('https://www.wikidata.org/w/api.php?', params).json() 
    qid = response.get('search')[0]['id']
    entity_qid_dict[entity] = qid
    return qid

In [6]:
def get_relation_pid(relation):
    params = dict (
            action='wbsearchentities',
            format='json',
            language='en',
            uselang='en',
            type='property',
            search= relation
            )

    response = requests.get('https://www.wikidata.org/w/api.php?', params).json() 
    return response.get('search')[0]['id']

In [7]:
get_relation_pid('synonym')

'P5973'

In [8]:
# load id -> path
sampled_problems = pickle.load(open(
            '/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/data/science/paths.pkl', 'rb'), encoding='latin1')

id_to_path = dict()
id_to_entities = dict()
print('loading problem plain texts')
for id_num in sampled_problems:
    f_short = sampled_problems[id_num]['forward']['short']
    r_short = sampled_problems[id_num]['reverse']['short']
    print(f_short)
    f_split = f_short.split()
    r_split = r_short.split()
    
    id_to_entities[id_num+'f'] = f_split[0::2]
    id_to_entities[id_num+'r'] = r_split[0::2]
    
    id_to_path[id_num+'f'] = f_short
    id_to_path[id_num+'r'] = r_short
    

loading problem plain texts
State <--Synonym--> Country <--RelatedTo--> Field <--RelatedTo--> Soccer 
Wave <--RelatedTo--> Part <--RelatedTo--> Range <--RelatedTo--> Measurement 
Number <--RelatedTo--> Unit <--RelatedTo--> Year <--RelatedTo--> Sun 
Number <--IsA-- Tenth <--RelatedTo--> Year <--RelatedTo--> Sun 
Mountain <--RelatedTo--> Part <--Synonym--> Office <--Antonym--> Home 
Wave <--RelatedTo--> Dream <--NotDesires-- Person --NotDesires--> Slip 
Part <--RelatedTo--> Hand <--RelatedTo--> People <--RelatedTo--> Life 
Purse --AtLocation--> Hand <--RelatedTo--> Member --IsA--> Unit 
Home <--RelatedTo--> Hill <--RelatedTo--> Gravity --IsA--> Force 
Paper <--RelatedTo--> Part <--Antonym--> Hand <--RelatedTo--> Food 
Purse --AtLocation--> House <--RelatedTo--> Type <--RelatedTo--> Unit 
Country <--Synonym--> Nation --IsA--> People <--IsA-- Community 
Street <--RelatedTo--> Home <--RelatedTo--> Country <--RelatedTo--> People 
Population --AtLocation--> Country <--RelatedTo--> State <--Re

Metal <--RelatedTo--> Surface <--RelatedTo--> Slip <--Synonym--> Trip 
Area <--Synonym--> Field <--RelatedTo--> Board <--RelatedTo--> Type 
Office <--RelatedTo--> People --AtLocation--> Doctor <--RelatedTo--> Job 
Field <--RelatedTo--> Land <--RelatedTo--> Country <--AtLocation-- Barn 
Box <--Synonym--> Field <--RelatedTo--> Country --IsA--> Area 
Home <--Synonym--> House --IsA--> Community <--RelatedTo--> People 
Point <--RelatedTo--> People --HasA--> Person <--IsA-- Job 
Hand <--RelatedTo--> Instrument <--RelatedTo--> Guitar 
Woman --IsA--> Person --CapableOf--> Hand <--RelatedTo--> Food 
Office <--RelatedTo--> Area <--RelatedTo--> Surface <--RelatedTo--> Board 
Home --AtLocation--> City <--DistinctFrom--> Country <--RelatedTo--> Category 
Instrument <--RelatedTo--> Hand <--AtLocation-- Molecule <--PartOf-- Chain 
Woman <--IsA-- Wave <--RelatedTo--> Hand <--RelatedTo--> Food 
Nation --IsA--> People <--RelatedTo--> Person --Desires--> Sugar 
Metal <--Antonym--> Stone <--RelatedTo--> H

In [9]:
len(id_to_entities)

5864

In [10]:
len(id_to_path)

5864

In [11]:
# vec = np.memmap("/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/Wikidata/embeddings/dimension_50/transe/entity2vec.bin" , dtype='float32', mode='r')
# id_to_embedding=vec.reshape(int(vec.shape[0]/50),50)
# id_to_embedding

In [12]:
with open("/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/Wikidata/embeddings/dimension_50/transe/entity2vec.bin", "rb") as f:
    id_to_embedding = np.fromfile(f,dtype=np.float32)
    id_to_embedding = id_to_embedding.reshape(int(id_to_embedding.shape[0]/50),50)

In [13]:
id_to_embedding

array([[ 0.154797,  0.245092,  0.395355, ..., -0.010872, -0.108721,
         0.117679],
       [ 0.117016,  0.050495, -0.001476, ..., -0.06967 ,  0.090583,
        -0.142975],
       [ 0.154163, -0.189461,  0.198401, ..., -0.082203, -0.119145,
        -0.271788],
       ...,
       [ 0.125119, -0.184034, -0.178899, ...,  0.027042,  0.080683,
         0.192526],
       [-0.190602,  0.042457, -0.158319, ..., -0.176787, -0.088293,
        -0.228254],
       [ 0.131009,  0.237184, -0.231747, ...,  0.083928, -0.048414,
        -0.082613]], dtype=float32)

In [14]:
### load Qid to id
qid_to_id = dict()
f = open("/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/Wikidata/knowledge graphs/entity2id.txt", 'r')
try:
    counter = 0
    for row in f:
        if counter%10000 == 0:
            print(counter)
        qid = row.split()[0]
        id = row.split()[1]
        qid_to_id[qid] = id
        counter += 1
finally:
    f.close()

0
10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1250000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1380000
13

10360000
10370000
10380000
10390000
10400000
10410000
10420000
10430000
10440000
10450000
10460000
10470000
10480000
10490000
10500000
10510000
10520000
10530000
10540000
10550000
10560000
10570000
10580000
10590000
10600000
10610000
10620000
10630000
10640000
10650000
10660000
10670000
10680000
10690000
10700000
10710000
10720000
10730000
10740000
10750000
10760000
10770000
10780000
10790000
10800000
10810000
10820000
10830000
10840000
10850000
10860000
10870000
10880000
10890000
10900000
10910000
10920000
10930000
10940000
10950000
10960000
10970000
10980000
10990000
11000000
11010000
11020000
11030000
11040000
11050000
11060000
11070000
11080000
11090000
11100000
11110000
11120000
11130000
11140000
11150000
11160000
11170000
11180000
11190000
11200000
11210000
11220000
11230000
11240000
11250000
11260000
11270000
11280000
11290000
11300000
11310000
11320000
11330000
11340000
11350000
11360000
11370000
11380000
11390000
11400000
11410000
11420000
11430000
11440000
11450000
11460000
1

19570000
19580000
19590000
19600000
19610000
19620000
19630000
19640000
19650000
19660000
19670000
19680000
19690000
19700000
19710000
19720000
19730000
19740000
19750000
19760000
19770000
19780000
19790000
19800000
19810000
19820000
19830000
19840000
19850000
19860000
19870000
19880000
19890000
19900000
19910000
19920000
19930000
19940000
19950000
19960000
19970000
19980000
19990000
20000000
20010000
20020000
20030000
20040000
20050000
20060000
20070000
20080000
20090000
20100000
20110000
20120000
20130000
20140000
20150000
20160000
20170000
20180000
20190000
20200000
20210000
20220000
20230000
20240000
20250000
20260000
20270000
20280000
20290000
20300000
20310000
20320000
20330000
20340000
20350000
20360000
20370000
20380000
20390000
20400000
20410000
20420000
20430000
20440000
20450000
20460000
20470000
20480000
20490000
20500000
20510000
20520000
20530000
20540000
20550000
20560000
20570000
20580000
20590000
20600000
20610000
20620000
20630000
20640000
20650000
20660000
20670000
2

In [15]:
len(qid_to_id)

20982733

In [16]:
def get_id_of_qid(qid):
    f = open("/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/Wikidata/knowledge graphs/entity2id.txt", 'r')
    for row in f:
        curr_qid = row.split()[0]
        if curr_qid == qid:
            return row.split()[1]

In [17]:
get_id_of_qid('Q27077071')

'20982732'

In [18]:
qid_to_id['Q27077071']

'20982732'

In [19]:
# Load graph embedding

# v_embed_dict = {}
# e_embed_dict = {}
# for line in load(v_embed_file):
#     word, embed = parse(line)
#     v_embed_dict[word] = embed

# for line in load(e_embed_file):
#     word, embed = parse(line)
#     e_embed_dict[word] = embed

v_id_embed_dict = {}
e_id_embed_dict = {}
# v_embed_for_unknown = np.random.randn(50, dtype=np.float32)
# e_embed_for_unknown = np.random.randn(50, dtype=np.float32)

counter = 0
for id in id_to_path.keys():
    counter += 1
    if counter%10 == 0:
        print(id)
#     v1, e1, v2, e2, v3, e3, v4= parse_path(id_to_path[id])
    v_id_embed_dict[id] = []
    for entity in id_to_entities[id]:
#         print(entity)
        qid = get_entity_qid(entity)
#         print(qid)
        if qid in qid_to_id:
            wiki_id = int(qid_to_id[qid])
#             print(wiki_id)
            curr_embed = list(id_to_embedding[wiki_id,:])
            v_id_embed_dict[id] += curr_embed
        else:
            v_id_embed_dict[id] += list(np.zeros(50, dtype = np.float32))
    if len(id_to_entities[id])<200:
        id_to_entities[id] += list(np.zeros(200-len(id_to_entities[id]), dtype=np.float32))
#     v_id_embed_dict[id] = [v_embed_dict[v1], ..., v_embed_dict[v4]]  # use v_embed_for_unknown for missing words
#     e_id_embed_dict[id] = [e_embed_dict[e1], e_embed_dict[e2], e_embed_dict[e3]]  # use e_embed_for_unknown for missing words



64610r
4449r
120614r
109055r
66771r
100387r
94209r
84862r
2311r
21100r
56056r
275r
90530r
46009r
124916r
124759r
118336r
98262r
33478r
101832r
54474r
123819r
123360r
104840r
14315r
83476r
111051r
96738r
58690r
18634r
79629r
109992r
1286r
83057r
61695r
108221r
2032r
103977r
47158r
96303r
118677r
92314r
107051r
113836r
6799r
59739r
117880r
3749r
105389r
124290r
90810r
107528r
116202r
72299r
104654r
49179r
87376r
118926r
45272r
70121r
70831r
48138r
62899r
121775r
119157r
109523r
59480r
28510r
32461r
20069r
115471r
59004r
97923r
111043r
66376r
67970r
123040r
63420r
73604r
126813r
93234r
110152r
35859r
124928r
116434r
65182r
51625r
40396r
45920r
95558r
117508r
119848r
69991r
121544r
49093r
13458r
125883r
114151r
27979r
118953r
53755r
102371r
55169r
118525r
24175r
71608r
119203r
5476r
45887r
102173r
68334r
67305r
85854r
111818r
79733r
109643r
86727r
95218r
94968r
32483r
26545r
126802r
109244r
93201r
110149r
107852r
110364r
84813r
56440r
98120r
25381r
55862r
101048r
51120r
86862r
116778r
2509

In [20]:
# id_to_embedding[426,:]

In [21]:
# save to features/ dicrector
with open("/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/code/science/features/v_kg_embed50.pkl", "wb") as output_file:
    cPickle.dump(v_id_embed_dict, output_file)
# pickle.dump(e_id_embed_dict, open("features/{xxxxx}.pkl", "rb"))

In [22]:
with open('/Users/songqifeng/Library/CloudStorage/OneDrive-NationalUniversityofSingapore/CS4248/project/concept-net/code/science/features/v_kg_embed50.pkl', 'rb') as handle:
    b = pickle.load(handle)

In [23]:
b

{'35540f': [0.177136,
  0.153836,
  -0.034931,
  0.20786,
  -0.006916,
  -0.133602,
  -0.131019,
  0.034476,
  -0.028148,
  0.130137,
  0.003347,
  -0.098866,
  -0.293087,
  0.093604,
  0.259879,
  -0.085103,
  0.111983,
  -0.150313,
  -0.275007,
  -0.078122,
  -0.133109,
  0.161528,
  0.170588,
  0.180147,
  0.162447,
  -0.085573,
  -0.104347,
  -0.081299,
  -0.005363,
  -0.064856,
  -0.016739,
  -0.076191,
  -0.132273,
  0.122839,
  -0.054301,
  -0.08131,
  -0.116686,
  -0.29874,
  0.097506,
  -0.195192,
  0.172974,
  -0.011248,
  -0.219327,
  -0.046259,
  -0.154161,
  -0.026467,
  0.069452,
  -0.102831,
  0.041142,
  0.252606,
  0.204224,
  0.077624,
  0.166734,
  -0.044832,
  -0.085835,
  0.163816,
  -0.201765,
  -0.026099,
  0.038398,
  0.072856,
  -0.059228,
  -0.023399,
  -0.14707,
  -0.033688,
  0.119357,
  0.280584,
  0.208349,
  -0.052303,
  0.039354,
  0.105572,
  -0.23607,
  -0.094101,
  -0.037809,
  0.177032,
  0.027359,
  -0.125764,
  -0.188384,
  -0.186683,
  -0.125161,


In [24]:
import json
  
with open('entity_to_qid.txt', 'w') as convert_file:
     convert_file.write(json.dumps(entity_qid_dict))